<a href="https://colab.research.google.com/github/anshulsolanki/stock_analysis/blob/main/stock-index_comparison.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# Install dependency if needed:
!pip install yfinance matplotlib

In [2]:
import yfinance as yf
import pandas as pd
import plotly.graph_objects as go

In [3]:
def do_comparison(index_symbol, stocks , index_name):
  # Download 5 years of data
  all_symbols = [index_symbol] + list(stocks.values())
  data = yf.download(all_symbols, period="5y")["Close"].ffill()

  # Time frames
  time_frames = {
      "1M": pd.DateOffset(months=1),
      "2M": pd.DateOffset(months=2),
      "3M": pd.DateOffset(months=3),
      "6M": pd.DateOffset(months=6),
      "1Y": pd.DateOffset(years=1),
      "3Y": pd.DateOffset(years=3),
      "5Y": pd.DateOffset(years=5),
  }

  # Create figure
  fig = go.Figure()

  # Add traces placeholders
  for stock in stocks.keys():
      fig.add_trace(go.Scatter(x=[], y=[], mode="lines", name=stock))

  # Add FMCG index as bold black line
  fig.add_trace(go.Scatter(x=[], y=[], mode="lines", name=index_name,
                          line=dict(color="black", width=3)))

  # Dropdown buttons
  buttons = []

  # Build performance table
  performance_table = pd.DataFrame(index=list(stocks.keys()) + [index_name])

  # Build RS table
  rs_table = pd.DataFrame(index=list(stocks.keys()))


  for label, offset in time_frames.items():
      today = data.index.max()
      start_date = today - offset
      df_slice = data[data.index >= start_date]

      # Normalize (start = 1)
      df_norm = df_slice / df_slice.iloc[0]

      # Collect data
      x_data, y_data = [], []

      performances ={}
      for stock, symbol in stocks.items():
          x_data.append(df_norm.index)
          y_data.append(df_norm[symbol])
          performances[stock] = df_norm[symbol].iloc[-1]  # final value

      # FMCG Index
      x_data.append(df_norm.index)
      y_data.append(df_norm[index_symbol])

      # Final normalized values for stocks
      performances = {stock: df_norm[symbol].iloc[-1] for stock, symbol in stocks.items()}

      # Add Nifty FMCG itself
      performances[index_name] = df_norm[index_symbol].iloc[-1]
      performance_table[label] = pd.Series(performances)
      performance_table = performance_table.round(3)

      # RS = Stock / Index
      rs_values = {
          stock: (df_norm[symbol].iloc[-1] / df_norm[index_symbol].iloc[-1])
          for stock, symbol in stocks.items()
      }

      rs_table[label] = pd.Series(rs_values)
      # Round for readability
      rs_table = rs_table.round(3)

      buttons.append(dict(
          label=label,
          method="update",
          args=[{"x": x_data, "y": y_data},
                {"title": f"Performance vs {index_name} ({label})"}]
      ))

  # Layout
  fig.update_layout(
      updatemenus=[dict(active=6, buttons=buttons, x=0.05, y=1.15, xanchor="left", yanchor="top")],
      title=f"Stock Performance vs {index_name}",
      xaxis_title="Date",
      yaxis_title="Normalized Performance",
      legend_title="Stocks"
  )

  fig.show()

  print("\n\n📊 Stock & Index Performance (End Value Normalized)")
  print(performance_table)

  #print(f"📊 Relative Strength (Stock vs {index_name})")
  #print(rs_table)


In [4]:
def do_RS_based_analysis(index_symbol, stocks):
  # Download 5-year data
  all_symbols = [index_symbol] + list(stocks.values())
  data = yf.download(all_symbols, period="5y")["Close"].ffill()

  # Define time frames
  time_frames = {
      "1M": pd.DateOffset(months=1),
      "2M": pd.DateOffset(months=2),
      "3M": pd.DateOffset(months=3),
      "6M": pd.DateOffset(months=6),
      "1Y": pd.DateOffset(years=1),
      "5Y": pd.DateOffset(years=5)
  }

  # Build Relative Strength table
  rs_table = pd.DataFrame(index=stocks.keys())
  today = data.index.max()

  for label, offset in time_frames.items():
      start_date = today - offset
      df_slice = data[data.index >= start_date]
      df_norm = df_slice / df_slice.iloc[0]  # normalize
      rs_values = {stock: df_norm[symbol].iloc[-1] / df_norm[index_symbol].iloc[-1]
                  for stock, symbol in stocks.items()}
      rs_table[label] = pd.Series(rs_values)

  rs_table = rs_table.round(3)
  print("\n📊 Relative Strength Table:")
  print(rs_table)

  # ---- Momentum Analysis ----
  # Consistent long-term outperformers (6M & 1Y RS > 1)
  rs_table['Consistent'] = (rs_table['1M'] > 1) & (rs_table['6M'] > 1) & (rs_table['1Y'] > 1)

  # Emerging outperformers (RS trending up: 3M → 2M → 1M)
  rs_table['Emerging'] = (rs_table['1M'] > rs_table['2M']) & (rs_table['2M'] > rs_table['3M'])

  # Slowing stocks (RS trending down: 3M → 2M → 1M)
  rs_table['Slowing'] = (rs_table['1M'] < rs_table['2M']) & (rs_table['2M'] < rs_table['3M'])

  # Optional: Overall score (Emerging + Consistent + latest RS)
  rs_table['Score'] = 0
  rs_table.loc[rs_table['Consistent'], 'Score'] += 1
  rs_table.loc[rs_table['Emerging'], 'Score'] += 1
  rs_table['Score'] += rs_table['1M']  # latest RS as part of score

  # Sort by score
  rs_table_sorted = rs_table.sort_values(by='Score', ascending=False)

  print("\n\n📊 RS Analysis with Momentum Flags (Emerging / Slowing / Consistent)")
  print(rs_table_sorted[['Consistent','Emerging','Slowing','Score']])

# **Index Comparison**

In [5]:
# Index and stocks
index_symbol = "^NSEI"  # Nifty 50

stocks = {
  "Nifty 50": "^NSEI",
  "Bank Nifty": "^NSEBANK",
  "Nifty IT": "^CNXIT",
  "Nifty Pharma": "^CNXPHARMA",
  "Nifty FMCG": "^CNXFMCG",
  "Nifty Auto": "^CNXAUTO",
  "Nifty Metal": "^CNXMETAL",
  "Nifty Realty": "^CNXREALTY",
  "Nifty Infra": "^CNXINFRA"
}
do_comparison(index_symbol, stocks,"Nifty 50" )
do_RS_based_analysis(index_symbol, stocks )

/tmp/ipython-input-2396573253.py:4: FutureWarning: YF.download() has changed argument auto_adjust default to True
  data = yf.download(all_symbols, period="5y")["Close"].ffill()
[*********************100%***********************]  9 of 9 completed




📊 Stock & Index Performance (End Value Normalized)
                 1M     2M     3M     6M     1Y     3Y     5Y
Nifty 50      1.002  0.964  0.996  1.113  0.974  1.404  2.147
Bank Nifty    0.971  0.940  0.966  1.122  1.050  1.374  2.268
Nifty IT      1.031  0.920  0.964  0.950  0.832  1.283  2.006
Nifty Pharma  0.989  0.988  1.018  1.096  0.947  1.735  1.921
Nifty FMCG    1.000  1.031  1.008  1.106  0.884  1.291  1.813
Nifty Auto    1.096  1.077  1.100  1.249  0.984  1.934  3.254
Nifty Metal   1.022  0.973  1.019  1.119  1.000  1.583  3.727
Nifty Realty  0.982  0.894  0.906  1.089  0.837  1.879  3.919
Nifty Infra   0.997  0.947  0.996  1.162  0.952  1.758  2.793
Nifty 50      1.002  0.964  0.996  1.113  0.974  1.404  2.147


/tmp/ipython-input-3553526634.py:4: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  9 of 9 completed



📊 Relative Strength Table:
                 1M     2M     3M     6M     1Y     5Y
Nifty 50      1.000  1.000  1.000  1.000  1.000  1.000
Bank Nifty    0.969  0.975  0.970  1.008  1.078  1.056
Nifty IT      1.029  0.955  0.968  0.853  0.854  0.935
Nifty Pharma  0.987  1.025  1.022  0.984  0.973  0.895
Nifty FMCG    0.997  1.069  1.012  0.994  0.907  0.844
Nifty Auto    1.093  1.117  1.104  1.122  1.010  1.516
Nifty Metal   1.020  1.009  1.023  1.005  1.026  1.736
Nifty Realty  0.979  0.927  0.909  0.978  0.859  1.825
Nifty Infra   0.995  0.982  1.000  1.044  0.977  1.301


📊 RS Analysis with Momentum Flags (Emerging / Slowing / Consistent)
              Consistent  Emerging  Slowing  Score
Nifty Auto          True     False    False  2.093
Nifty Metal         True     False    False  2.020
Nifty Realty       False      True    False  1.979
Nifty IT           False     False    False  1.029
Nifty 50           False     False    False  1.000
Nifty FMCG         False     False    False  0

#FMCG sector analysis

In [6]:
# Index and stocks
index_symbol = "^CNXFMCG"  # Nifty FMCG
stocks = {
    "Britannia": "BRITANNIA.NS",
    "Colgate Palmolive": "COLPAL.NS",
    "Dabur": "DABUR.NS",
    "HUL": "HINDUNILVR.NS",
    "Gillette": "GILLETTE.NS",
    "ITC": "ITC.NS",
    "Marico": "MARICO.NS",
    "Nestle India": "NESTLEIND.NS",
    "Godrej Consumer": "GODREJCP.NS",
    "Tata Consumer": "TATACONSUM.NS",
    "Varun Beverages": "VBL.NS"
}
do_comparison(index_symbol, stocks,"Nifty FMCG" )
do_RS_based_analysis(index_symbol, stocks )

/tmp/ipython-input-2396573253.py:4: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  12 of 12 completed


/tmp/ipython-input-3553526634.py:4: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[                       0%                       ]



📊 Stock & Index Performance (End Value Normalized)
                      1M     2M     3M     6M     1Y     3Y     5Y
Britannia          1.022  1.031  1.057  1.289  1.000  1.641  1.680
Colgate Palmolive  1.045  0.979  0.954  0.980  0.663  1.498  1.918
Dabur              0.980  1.096  1.092  1.076  0.835  0.951  1.130
HUL                1.038  1.154  1.129  1.230  0.967  1.069  1.326
Gillette           0.944  0.940  1.068  1.294  1.150  1.930  2.038
ITC                0.975  0.978  0.968  1.040  0.823  1.408  2.590
Marico             1.028  1.030  1.049  1.243  1.141  1.449  2.121
Nestle India       1.032  0.979  0.980  1.079  0.946  1.248  1.566
Godrej Consumer    0.996  1.080  0.997  1.269  0.869  1.407  1.972
Tata Consumer      1.005  0.982  0.960  1.136  0.903  1.316  2.039
Varun Beverages    0.968  1.098  1.029  1.087  0.816  2.392  7.387
Nifty FMCG         1.000  1.031  1.008  1.106  0.884  1.291  1.813


[*********************100%***********************]  12 of 12 completed


📊 Relative Strength Table:
                      1M     2M     3M     6M     1Y     5Y
Britannia          1.022  1.001  1.048  1.165  1.132  0.927
Colgate Palmolive  1.046  0.950  0.946  0.886  0.750  1.058
Dabur              0.980  1.064  1.083  0.972  0.945  0.624
HUL                1.038  1.120  1.120  1.112  1.095  0.731
Gillette           0.944  0.912  1.059  1.170  1.302  1.124
ITC                0.975  0.949  0.960  0.940  0.932  1.429
Marico             1.029  0.999  1.040  1.124  1.291  1.170
Nestle India       1.032  0.950  0.972  0.976  1.070  0.864
Godrej Consumer    0.997  1.048  0.989  1.147  0.983  1.088
Tata Consumer      1.005  0.953  0.953  1.027  1.022  1.125
Varun Beverages    0.968  1.065  1.021  0.983  0.924  4.075


📊 RS Analysis with Momentum Flags (Emerging / Slowing / Consistent)
                   Consistent  Emerging  Slowing  Score
Colgate Palmolive       False      True    False  2.046
HUL                      True     False    False  2.038
Marico        

In [7]:
# Index and stocks
index_symbol = "^NSEBANK"  # Nifty FMCG
stocks = {
    "HDFC": "HDFCBANK.NS",
    "ICICI": "ICICIBANK.NS",
    "SBI": "SBIN.NS",
    "Kotak": "KOTAKBANK.NS",
    "Axis": "AXISBANK.NS",
    "BOB": "BANKBARODA.NS",
    "IDFC First": "IDFCFIRSTB.NS",
    "Federal Bank India": "FEDERALBNK.NS"
}
do_comparison(index_symbol, stocks,"Nifty Bank" )
do_RS_based_analysis(index_symbol, stocks )

/tmp/ipython-input-2396573253.py:4: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  9 of 9 completed


/tmp/ipython-input-3553526634.py:4: FutureWarning:

YF.download() has changed argument auto_adjust default to True





📊 Stock & Index Performance (End Value Normalized)
                       1M     2M     3M     6M     1Y     3Y     5Y
HDFC                0.945  0.945  0.995  1.130  1.181  1.373  1.843
ICICI               0.966  0.993  0.980  1.179  1.156  1.654  3.732
SBI                 1.015  0.983  0.991  1.183  1.000  1.598  4.005
Kotak               0.988  0.903  0.955  1.029  1.107  1.038  1.382
Axis                0.999  0.905  0.889  1.055  0.894  1.430  2.195
BOB                 0.997  0.947  0.952  1.238  0.955  1.924  5.561
IDFC First          1.020  0.895  1.007  1.199  0.922  1.407  2.203
Federal Bank India  0.993  0.890  0.944  1.085  1.000  1.662  3.706
Nifty Bank          0.971  0.940  0.966  1.122  1.050  1.374  2.268


[*********************100%***********************]  9 of 9 completed



📊 Relative Strength Table:
                       1M     2M     3M     6M     1Y     5Y
HDFC                0.973  1.005  1.030  1.006  1.125  0.813
ICICI               0.995  1.057  1.015  1.050  1.101  1.645
SBI                 1.046  1.046  1.026  1.054  0.953  1.766
Kotak               1.018  0.960  0.989  0.917  1.055  0.609
Axis                1.029  0.963  0.921  0.940  0.851  0.968
BOB                 1.027  1.008  0.985  1.103  0.910  2.452
IDFC First          1.051  0.953  1.042  1.068  0.878  0.971
Federal Bank India  1.023  0.947  0.977  0.967  0.953  1.634


📊 RS Analysis with Momentum Flags (Emerging / Slowing / Consistent)
                    Consistent  Emerging  Slowing  Score
Axis                     False      True    False  2.029
BOB                      False      True    False  2.027
IDFC First               False     False    False  1.051
SBI                      False     False    False  1.046
Federal Bank India       False     False    False  1.023
Kotak      

In [8]:
index_symbol = "^CNXAUTO"  # Nifty Auto

stocks = {
    "Maruti Suzuki India": "MARUTI.NS",
    "Tata Motors": "TATAMOTORS.NS",
    "Mahindra & Mahindra": "M&M.NS",
    "Bajaj Auto": "BAJAJ-AUTO.NS",
    "Eicher Motors": "EICHERMOT.NS",
    "TVS Motor Company": "TVSMOTOR.NS",
    "Hero MotoCorp": "HEROMOTOCO.NS",
    "Ashok Leyland": "ASHOKLEY.NS",
    "Force Motors": "FORCEMOT.NS",
    "SML Isuzu": "SMLISUZU.NS"
}
do_comparison(index_symbol, stocks,"Nifty auto" )
do_RS_based_analysis(index_symbol, stocks )

/tmp/ipython-input-2396573253.py:4: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  11 of 11 completed


/tmp/ipython-input-3553526634.py:4: FutureWarning:

YF.download() has changed argument auto_adjust default to True





📊 Stock & Index Performance (End Value Normalized)
                        1M     2M     3M     6M     1Y      3Y      5Y
Maruti Suzuki India  1.210  1.209  1.224  1.278  1.211   1.699   2.249
Tata Motors          1.064  1.009  0.978  1.121  0.637   1.500   4.871
Mahindra & Mahindra  1.049  1.052  1.104  1.280  1.203   2.593   5.720
Bajaj Auto           1.115  1.068  1.080  1.192  0.826   2.343   3.466
Eicher Motors        1.136  1.113  1.187  1.297  1.295   1.906   3.091
TVS Motor Company    1.174  1.160  1.215  1.450  1.208   3.350   7.813
Hero MotoCorp        1.216  1.260  1.258  1.466  0.978   2.015   2.059
Ashok Leyland        1.064  1.018  1.084  1.247  1.037   1.647   3.916
Force Motors         1.143  1.296  1.641  2.749  2.304  15.036  17.943
SML Isuzu            1.177  1.838  2.165  3.646  2.060   5.506   9.897
Nifty auto           1.096  1.077  1.100  1.249  0.984   1.934   3.254


[*********************100%***********************]  11 of 11 completed



📊 Relative Strength Table:
                        1M     2M     3M     6M     1Y     5Y
Maruti Suzuki India  1.104  1.123  1.113  1.023  1.230  0.691
Tata Motors          0.970  0.937  0.889  0.897  0.647  1.497
Mahindra & Mahindra  0.957  0.977  1.004  1.024  1.223  1.758
Bajaj Auto           1.017  0.991  0.982  0.954  0.840  1.065
Eicher Motors        1.036  1.033  1.079  1.038  1.316  0.950
TVS Motor Company    1.071  1.077  1.104  1.161  1.227  2.401
Hero MotoCorp        1.110  1.170  1.143  1.174  0.994  0.633
Ashok Leyland        0.971  0.945  0.985  0.998  1.053  1.204
Force Motors         1.042  1.203  1.492  2.201  2.341  5.514
SML Isuzu            1.074  1.707  1.968  2.918  2.093  3.042


📊 RS Analysis with Momentum Flags (Emerging / Slowing / Consistent)
                     Consistent  Emerging  Slowing  Score
Maruti Suzuki India        True     False    False  2.104
SML Isuzu                  True     False     True  2.074
TVS Motor Company          True     False     